# Φ<sub>Flow</sub> Animation Gallery

This notebook shows various animations created with [Φ-Flow](https://github.com/tum-pbs/PhiFlow).

[**Documentation**](https://tum-pbs.github.io/PhiFlow/)
&nbsp;&nbsp;&nbsp; [**API**](https://tum-pbs.github.io/PhiFlow/phi)
&nbsp;&nbsp;&nbsp; [**Demos**](https://github.com/tum-pbs/PhiFlow/tree/develop/demos)

In [ ]:
!pip install --upgrade --quiet git+https://github.com/tum-pbs/PhiFlow@2.2-develop  # Install latest version, might be unstable

In [2]:
from phi.torch.flow import *

## Line Plots

We define the sine waves $\sin(x - t)$ and $\sin(x + t)$ and sample them on a grid from $x=0$ to $x=2\pi$ with resolution $R_x = 100$.
This is done for 60 values of $t$, linearly spaced between $0$ and $4\pi$.
These curves are animated in the left plot and their sum, a standing wave, is plotted on the right.

In [3]:
curves = CenteredGrid(lambda x, t: math.stack([math.sin(x - t), math.cos(x + t)], channel('c')), x=100, t=60, bounds=Box(x=2*PI, t=4*PI)).t[:-1]
vis.plot({"Curves": curves, "Sum": sum(curves.c)}, animate='t')

<Figure size 432x288 with 0 Axes>

# Geometric Primitives

In [3]:
vis.plot(Sphere(x=wrap([0, 2], instance(spheres='Left,Right')), y=0, radius=math.linspace(0, 1, batch(time=50))**.5), animate='time')

<Figure size 432x288 with 0 Axes>

In [5]:
x = math.range(instance(boxes=10))
vis.plot(Box(x=(x, x+1), y=(0, 2 * math.sin(math.linspace(0, 2*PI, batch(time=30)) + x*.5))), animate='time')

<Figure size 432x288 with 0 Axes>

## Quiver Plots

Vectors at arbitrary locations using `PointCloud`

In [ ]:
x = math.rotate_vector(math.vec(x=1, y=0), angle=math.linspace(0, 2*PI, spatial(points=50)))
dx, x = x.points[1:] - x.points[:-1], x.points[:-1]
vis.plot(vis.overlay(PointCloud(x, dx), math.rename_dims(PointCloud(x, dx, color='#40FFFF'), 'points', 'time')), animate='time')

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:3: RuntimeWarning: rename_dims() default implementation is slow on large dimensions ((pointsˢ=49)). Please implement __replace_dims__()
  This is separate from the ipykernel package so we can avoid doing imports until


<Figure size 432x288 with 0 Axes>

## 2D Scalar Noise

Here we visualize the built-in class `Noise`, sampling it on a $64^3$ grid ranging from 0 to 10 along each axis. We plot all $x$-$y$ slices over time, yielding a scanning animation.
The left plot shows noise with a smoothness of 1.0 and the right plot shows the same random noise (equal seed) with smoothness of 1.3.

In [ ]:
noise = Noise(smoothness=math.stack({"Default Noise": 1.0, "Smooth Noise": 1.3}, batch('c')))
grid = CenteredGrid(noise, x=64, y=64, z=64, bounds=Box(x=10, y=10, z=10))
vis.plot(grid, animate='z', show_color_bar=False)

<Figure size 432x288 with 0 Axes>

## Solar System
Geometric Primitives

In [ ]:
PLANETS = instance(planets='Sun,Earth,Mars')
x = math.rename_dims(math.stack({'Sun': (0, 0), 'Earth': (9, 0), 'Mars': (0, 12)}, PLANETS), 'vector', channel(vector='x,y'))
x = math.rotate_vector(x, math.linspace(0, wrap([0, 5, 3], PLANETS), batch(time=130)))
vis.plot(PointCloud(Sphere(x, radius=wrap([1, .4, .2], PLANETS))), animate='time')

/usr/local/lib/python3.7/dist-packages/phi/math/_ops.py:383: UserWarning: dim.split() is deprecated. Use math.split_dims() instead.
  return wrap(result).vector.split(shape)


<Figure size 432x288 with 0 Axes>

## 3D Voxels

Two spheres are placed in a $32^3$ domain, at positions (16, 16, 0) and (16, 16, 32). Their radii grow linearly in time.
These spheres are then sampled on a regular grid and plotted as voxels.
Additionally, we plot the cross section $y=16$ as a 2D heat map.

In [ ]:
sphere = Sphere(x=16, y=16, z=0, radius=math.linspace(0, 16, batch(time=17)))
grid = CenteredGrid(union(sphere, sphere.shifted((0, 0, 32))), x=32, y=32, z=32)
vis.plot({"3D": grid, "2D Slice": grid.y[16]}, animate='time', frame_time=300)

<Figure size 432x288 with 0 Axes>

## Spirals

In [ ]:
dst = math.linspace(0, 1, instance(points=200))
angle = math.linspace(0, math.linspace(0, 20, batch(time=100)), dst.shape)
vis.plot(PointCloud(dst * math.vec(x=math.cos(angle), y=math.sin(angle))), animate='time')

<Figure size 432x288 with 0 Axes>

In [ ]:
dst = math.linspace(0, 1, instance(points=200))
angle = math.linspace(0, math.linspace(PI*200, 1.1*PI*200, batch(time=200)), dst.shape)
vis.plot(PointCloud(dst * math.vec(x=math.cos(angle), y=math.sin(angle))), animate='time')

<Figure size 432x288 with 0 Axes>

## Bouncing Balls

This demo visualizes the evolution of a `PointCloud` as a 3D scatter plot animation.

Thirty balls are placed at random locations. The initial velocities are sampled from a normal distribution with standard deviations $\sigma_x = \sigma_y = 1$ and $\sigma_z = 2$.

A simulation is than run for 100 frames, performing the following operations at each step:

* Gravity is applied, $g_z = -9.81$,
* Friction is computed proportional to velocity,
* The balls are advected using Euler integration,
* When below $z=0$, the y velocity is negated to simulate an elastic collision with the floor.

In [ ]:
balls = PointCloud(Sphere(math.random_uniform(instance(balls=30), channel(vector='x,y,z')) + 5, radius=.1), math.random_normal(instance(balls=30), channel(vector='x,y,z')) * (1, 1, 2))
def step(balls, dt=.1):
  balls *= math.where(balls.points.vector['z'] < 0, (1, 1, -1), 1) * 0.7 ** dt
  return advect.points(balls, balls, dt) + (0, 0, -9.81 * dt)
vis.plot(math.iterate(step, batch(time=100), balls).mask(), animate='time')

<Figure size 432x288 with 0 Axes>

## Burgers' Equation

Grid quiver plots

In [ ]:
velocity = CenteredGrid(Noise(smoothness=1.5, vector='x,y'), extrapolation.PERIODIC, x=64, y=64) * 2
def burgers(v, dt=.5):
    return diffuse.explicit(advect.semi_lagrangian(v, v, dt), .08, dt)
vis.plot(math.iterate(burgers, batch(time=100), velocity), animate='time')

<Figure size 432x288 with 0 Axes>

## Incompressible Flow

In [ ]:
def incompressible_fluid_step(v: StaggeredGrid, p: CenteredGrid, dt=.5):
    return fluid.make_incompressible(advect.advect(v, v, dt), (), Solve('auto', 1e-5, 1e-5, x0=p))
trj = math.iterate(incompressible_fluid_step, batch(time=40), *fluid.make_incompressible(StaggeredGrid(Noise(), 0, x=64, y=64)))
vis.plot({"Vorticity": field.curl(trj[0]), "Pressure": trj[1]}, animate='time', same_scale=False)

<Figure size 432x288 with 0 Axes>

## Reaction-Diffusion

In [ ]:
def reaction_diffusion(u, v, du=.19, dv=.05, f=.06, k=.062, dt=1.):
    return u + dt * du * field.laplace(u) - u * v**2 + f * (1 - u), v + dt * dv * field.laplace(v) + u * v**2 - (f + k) * v
trj_u, trj_v = math.iterate(reaction_diffusion, batch(time=1000), *[CenteredGrid(Noise(scale=20, smoothness=1.3), x=100, y=100) * .2 + .5]*2)
vis.plot(trj_u.time[::10], animate='time')

<Figure size 432x288 with 0 Axes>